In [28]:
import cv2
import glob
import os
import tqdm
import pybboxes as pbx
import numpy as np

#Save the image file
output_dark = "/home/ubuntum/Desktop/dark_helmet/"
output_light = "/home/ubuntum/Desktop/light_helmet/"

# Load the image file
image_folder = "/home/ubuntum/Desktop/helmet/helmet/"
image_files = sorted(glob.glob(os.path.join(image_folder, '*.jpg')))

# Load the text file
#txt_files = sorted(glob.glob("/home/ubuntum/Desktop/helmet/helmet_labels/*.txt"))



write_to_light_folder = False 
for image_file in tqdm.tqdm(image_files[:20000]):
   
    #image file and corresponding txt file to image
    image_basename = os.path.basename(image_file)
    txt_basename = os.path.splitext(image_basename)[0] + ".txt"
    txt_file = os.path.join("/home/ubuntum/Desktop/helmet/helmet_labels/", txt_basename)
    #print(txt_file)
    #print(image_file)
    with open(txt_file, 'r') as file:
        #print(txt_file)
        #print(image_file)
        lines = file.readlines()
        bboxes = []
        for line in lines:
            line = line.strip().split(" ")

            try:
                if int(line[0]) == 18:

                    # Load the image 
                    image = cv2.imread(image_file)

                    image_height, image_width  = image.shape[:2]
                    bbox = [float(x) for x in line[1:]]
                    
                    if int(line[0]) == 18:
                        box = pbx.convert_bbox(bbox, from_type='yolo', to_type='voc', image_size=(image_width,image_height))
                        bboxes.append(box)
                        

                else:
                    continue
            except ValueError:
                    #skip the line if the first element is not a valid integer
                    continue
        image_classified = False
        for bbox in bboxes:
            
            # Calculate the height of the ROI
            roi_height = bbox[3] - bbox[1]

            # Calculate the top and bottom y coordinates for the middle-upper part of the ROI
            middle_upper_y1 = bbox[1]
            middle_upper_y2 = int(bbox[1] + roi_height * 1)

            # Set vertical offset for cropping
            offset = 1

            # Extract ROI from image
            roi = image[bbox[1]:bbox[3], bbox[0]:bbox[2]]
            
            # Apply thresholding to ROI
            try:
                # Convert ROI to HSV color space
                hsv = cv2.cvtColor(roi, cv2.COLOR_BGR2HSV)
                # Split into individual channels
                hue, saturation, values = cv2.split(hsv)
                # Apply adaptive thresholding to value channel
                thresh_value = cv2.adaptiveThreshold(hue, 255, cv2.ADAPTIVE_THRESH_GAUSSIAN_C, cv2.THRESH_BINARY, 5, 2)
                
                # Crop the right and left upper corners of the thresholded image
                #cropped_thresh_value = thresh_value[:, 1:-1]
                #cropped_thresh_value2 = cropped_thresh_value[offset:, :]
                # Merge thresholded value channel with hue and saturation
                segmented = thresh_value, saturation, values
                
                #Show threshold image
                #if cropped_thresh_value2.shape[0] > 0 and cropped_thresh_value2.shape[1] > 0:
                #    cv2.imshow("threshold", cropped_thresh_value2)
                #    cv2.waitKey(0)

                # Calculate the number of pixels in the thresholded image inside the bounding box
                num_pixels = np.sum(segmented[2] > 0)
            
                # Determine how many pixels are close to black and how many are close to white
                num_black_pixels = np.sum(segmented[2] < 60)

                num_white_pixels = num_pixels - num_black_pixels
                new_num_white_pixels = abs(num_white_pixels)
                white_percentage = (new_num_white_pixels * 100) / num_pixels 

                print("sum of  pixels:", image_file,  num_pixels)
                print("sum of black pixels:", num_black_pixels)
                print("sum of white pixels:", new_num_white_pixels)
                print("white percentage:", white_percentage)

                if white_percentage > 60:
                    
                    #base_name, ext = os.path.splitext(os.path.basename(image_file))
                    #out_light = os.path.join(output_light, f"{base_name}{ext}")          
                    #cv2.imwrite(out_light, image)
                    image_classified = True
                    break

            except cv2.error as e:
                print(f"cv2.cvtColor() error: {e}")
                print(image_file)
                continue

        
        # Check if image has already been classified
        if not image_classified:
            # Save image to out_dark folder               
            base_name, ext = os.path.splitext(os.path.basename(image_file))
            out_dark = os.path.join(output_dark, f"{base_name}{ext}")          
            cv2.imwrite(out_dark, image)
cv2.destroyAllWindows()


  0%|          | 6/20000 [00:00<06:49, 48.86it/s]

sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00000020.jpg 6804
sum of black pixels: 2620
sum of white pixels: 4184
white percentage: 61.493239271017046
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00000035.jpg 4263
sum of black pixels: 756
sum of white pixels: 3507
white percentage: 82.26600985221675
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00000046.jpg 7550
sum of black pixels: 3951
sum of white pixels: 3599
white percentage: 47.66887417218543
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00000058.jpg 3658
sum of black pixels: 1233
sum of white pixels: 2425
white percentage: 66.29305631492619
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00000081.jpg 49
sum of black pixels: 16
sum of white pixels: 33
white percentage: 67.34693877551021
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00000090.jpg 1349
sum of black pixels: 300
sum of white pixels: 1049
white perce

  0%|          | 21/20000 [00:00<05:07, 65.03it/s]

sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00000219.jpg 4071
sum of black pixels: 737
sum of white pixels: 3334
white percentage: 81.89633996561041
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00000247.jpg 4015
sum of black pixels: 535
sum of white pixels: 3480
white percentage: 86.6749688667497
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00000258.jpg 2450
sum of black pixels: 295
sum of white pixels: 2155
white percentage: 87.95918367346938
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00000260.jpg 612
sum of black pixels: 274
sum of white pixels: 338
white percentage: 55.22875816993464
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00000265.jpg 513
sum of black pixels: 332
sum of white pixels: 181
white percentage: 35.28265107212476
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00000265.jpg 780
sum of black pixels: 407
sum of white pixels: 373
white percentage:

  0%|          | 35/20000 [00:00<05:28, 60.71it/s]

...

sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00364871.jpg 96
sum of black pixels: 17
sum of white pixels: 79
white percentage: 82.29166666666667
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00364884.jpg 5590
sum of black pixels: 3821
sum of white pixels: 1769
white percentage: 31.645796064400717
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00364885.jpg 18864
sum of black pixels: 1160
sum of white pixels: 17704
white percentage: 93.85072094995759
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00364897.jpg 5346
sum of black pixels: 23
sum of white pixels: 5323
white percentage: 99.56977179199401
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00364908.jpg 2464
sum of black pixels: 325
sum of white pixels: 2139
white percentage: 86.81006493506493
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00364951.jpg 550
sum of black pixels: 83
sum of white pixels: 467
white percenta

100%|█████████▉| 19984/20000 [04:13<00:00, 96.34it/s] 

sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00365286.jpg 315
sum of black pixels: 0
sum of white pixels: 315
white percentage: 100.0
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00365287.jpg 3420
sum of black pixels: 1526
sum of white pixels: 1894
white percentage: 55.380116959064324
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00365287.jpg 3392
sum of black pixels: 405
sum of white pixels: 2987
white percentage: 88.06014150943396
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00365295.jpg 1053
sum of black pixels: 357
sum of white pixels: 696
white percentage: 66.0968660968661
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00365298.jpg 986
sum of black pixels: 152
sum of white pixels: 834
white percentage: 84.5841784989858
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00365300.jpg 3416
sum of black pixels: 1576
sum of white pixels: 1840
white percentage: 53.8641686

100%|██████████| 20000/20000 [04:13<00:00, 78.95it/s]

sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00365621.jpg 1333
sum of black pixels: 52
sum of white pixels: 1281
white percentage: 96.09902475618905
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00365647.jpg 170
sum of black pixels: 44
sum of white pixels: 126
white percentage: 74.11764705882354
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00365658.jpg 493
sum of black pixels: 199
sum of white pixels: 294
white percentage: 59.63488843813388
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00365706.jpg 10239
sum of black pixels: 1916
sum of white pixels: 8323
white percentage: 81.28723508155093
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00365735.jpg 12028
sum of black pixels: 136
sum of white pixels: 11892
white percentage: 98.86930495510475
sum of  pixels: /home/ubuntum/Desktop/helmet/helmet/objects365_v1_00365778.jpg 638
sum of black pixels: 294
sum of white pixels: 344
white percenta